# Application des filtres bayésiens pour la prédiction de la volatilité

### I - Importation et traitement des données

On commence par importer tous les modules nécessaires.

In [91]:
import pandas as pd
import numpy as np
from pathlib import Path
from stats import *
import warnings 
warnings.simplefilter('ignore')
import plotly.graph_objects as go
from gaussians import gaussian

On importe nos 5 séries de prix à la minute à partir de leurs fichiers .csv respectifs.

In [92]:
df_cryptos = pd.DataFrame()
cryptos = ['BTC','ETH','LTC','XRP','BCH']
for crypto in cryptos:
    path = Path(f'../Data/Data 1 min/{crypto}_USDT_binance_1m_2020-02-24_2021-04-30.csv')
    if path.exists():
        data = pd.read_csv(path)
        df_cryptos[crypto] = data['close']
    else:
        print(f"File not found: {path}")
df_cryptos.set_index(data['timestamp'], inplace=True)
df_cryptos.sort_values('timestamp', inplace=True)
df_cryptos.head(5)

BTC     ETH    LTC      XRP     BCH
timestamp                                                   
2020-02-24 00:00:00  9935.18  274.31  79.35  0.28272  400.46
2020-02-24 00:01:00  9939.15  274.43  79.40  0.28309  400.81
2020-02-24 00:02:00  9910.94  274.01  79.20  0.28267  400.08
2020-02-24 00:03:00  9914.81  273.79  79.23  0.28264  400.67
2020-02-24 00:04:00  9922.56  273.68  79.11  0.28207  401.08

A partir des séries temporelles des prix, on calcules rendements logarithmiques de chaque actif.

In [93]:
df_log_returns = np.log(df_cryptos / df_cryptos.shift(1)).dropna()
df_log_returns.head(5)

BTC       ETH       LTC       XRP       BCH
timestamp                                                            
2020-02-24 00:01:00  0.000400  0.000437  0.000630  0.001308  0.000874
2020-02-24 00:02:00 -0.002842 -0.001532 -0.002522 -0.001485 -0.001823
2020-02-24 00:03:00  0.000390 -0.000803  0.000379 -0.000106  0.001474
2020-02-24 00:04:00  0.000781 -0.000402 -0.001516 -0.002019  0.001023
2020-02-24 00:05:00  0.000390  0.000694 -0.000126  0.000284  0.000798

A partir des prix on calcule les variances des actifs ainsi que leurs covariances.

In [94]:
df_var_cov = pd.DataFrame()
for i in range(len(cryptos)):
    for j in range(i, len(cryptos)):
        if i == j:
            df_var_cov[f'Variance {cryptos[i]}'] = hourly_var(df_cryptos[[cryptos[i]]])
        else:
            df_var_cov[f'Covariance {cryptos[i]} - {cryptos[j]}'] = hourly_cov(df_cryptos[[cryptos[i], cryptos[j]]])

if df_var_cov.isnull().values.any():
    df_var_cov.interpolate(method='linear', inplace=True)
df_var_cov *= 100
df_var_cov.head(5)

Variance BTC  Covariance BTC - ETH  Covariance BTC - LTC  \
Timestamp                                                                       
2020-02-24 00:00:00      0.003562              0.003615              0.003769   
2020-02-24 01:00:00      0.002334              0.002460              0.002598   
2020-02-24 02:00:00      0.023011              0.018212              0.032670   
2020-02-24 03:00:00      0.002530              0.003015              0.003682   
2020-02-24 04:00:00      0.001550              0.001989              0.001750   

                     Covariance BTC - XRP  Covariance BTC - BCH  Variance ETH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.002974              0.004944      0.006456   
2020-02-24 01:00:00              0.002192              0.003045      0.004312   
2020-02-24 02:00:00              0.030234              0.033199      0.017474   
2020-02-24 03:00:00              0.003008              0.003910      0.004914   
2020-02-24 04:00:00              0.001502              0.002233      0.004236   

                     Covariance ETH - LTC  Covariance ETH - XRP  \
Timestamp                                                         
2020-02-24 00:00:00              0.005494              0.004639   
2020-02-24 01:00:00              0.003471              0.002857   
2020-02-24 02:00:00              0.028066              0.025975   
2020-02-24 03:00:00              0.005075              0.004252   
2020-02-24 04:00:00              0.002850              0.002298   

                     Covariance ETH - BCH  Variance LTC  Covariance LTC - XRP  \
Timestamp                                                                       
2020-02-24 00:00:00              0.006757      0.007723              0.004649   
2020-02-24 01:00:00              0.004696      0.007448              0.003595   
2020-02-24 02:00:00              0.029274      0.057310              0.050088   
2020-02-24 03:00:00              0.005020      0.012367              0.006036   
2020-02-24 04:00:00              0.004074      0.004465              0.001664   

                     Covariance LTC - BCH  Variance XRP  Covariance XRP - BCH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.007227      0.005516              0.005156   
2020-02-24 01:00:00              0.005598      0.003440              0.003720   
2020-02-24 02:00:00              0.054307      0.053296              0.053748   
2020-02-24 03:00:00              0.007733      0.006066              0.005727   
2020-02-24 04:00:00              0.003079      0.003474              0.002697   

                     Variance BCH  
Timestamp                          
2020-02-24 00:00:00      0.012095  
2020-02-24 01:00:00      0.011074  
2020-02-24 02:00:00      0.062093  
2020-02-24 03:00:00      0.009839  
2020-02-24 04:00:00      0.006102

### II - Application du filtre de Kalman sur un modèle SS-ARIMA appliqué à la variance horaire

On garde les variances de la période de Covid-19.

In [95]:
start_date = "2020-02-26 00:00:00"
end_date = "2021-04-18 00:00:00"

covid_var = df_var_cov[(df_var_cov.index >= start_date) & (df_var_cov.index <= end_date)]

df_var_cov.head(5)

Variance BTC  Covariance BTC - ETH  Covariance BTC - LTC  \
Timestamp                                                                       
2020-02-24 00:00:00      0.003562              0.003615              0.003769   
2020-02-24 01:00:00      0.002334              0.002460              0.002598   
2020-02-24 02:00:00      0.023011              0.018212              0.032670   
2020-02-24 03:00:00      0.002530              0.003015              0.003682   
2020-02-24 04:00:00      0.001550              0.001989              0.001750   

                     Covariance BTC - XRP  Covariance BTC - BCH  Variance ETH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.002974              0.004944      0.006456   
2020-02-24 01:00:00              0.002192              0.003045      0.004312   
2020-02-24 02:00:00              0.030234              0.033199      0.017474   
2020-02-24 03:00:00              0.003008              0.003910      0.004914   
2020-02-24 04:00:00              0.001502              0.002233      0.004236   

                     Covariance ETH - LTC  Covariance ETH - XRP  \
Timestamp                                                         
2020-02-24 00:00:00              0.005494              0.004639   
2020-02-24 01:00:00              0.003471              0.002857   
2020-02-24 02:00:00              0.028066              0.025975   
2020-02-24 03:00:00              0.005075              0.004252   
2020-02-24 04:00:00              0.002850              0.002298   

                     Covariance ETH - BCH  Variance LTC  Covariance LTC - XRP  \
Timestamp                                                                       
2020-02-24 00:00:00              0.006757      0.007723              0.004649   
2020-02-24 01:00:00              0.004696      0.007448              0.003595   
2020-02-24 02:00:00              0.029274      0.057310              0.050088   
2020-02-24 03:00:00              0.005020      0.012367              0.006036   
2020-02-24 04:00:00              0.004074      0.004465              0.001664   

                     Covariance LTC - BCH  Variance XRP  Covariance XRP - BCH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.007227      0.005516              0.005156   
2020-02-24 01:00:00              0.005598      0.003440              0.003720   
2020-02-24 02:00:00              0.054307      0.053296              0.053748   
2020-02-24 03:00:00              0.007733      0.006066              0.005727   
2020-02-24 04:00:00              0.003079      0.003474              0.002697   

                     Variance BCH  
Timestamp                          
2020-02-24 00:00:00      0.012095  
2020-02-24 01:00:00      0.011074  
2020-02-24 02:00:00      0.062093  
2020-02-24 03:00:00      0.009839  
2020-02-24 04:00:00      0.006102

A partir des variances des actifs durant la période de crise sanitaire on estime le modèle ARIMA optimal. Pour déterminer l'ordre d'intégration optimal, on applique le test de KPSS en boucle en intégrant la série temporelle jusqu'à ce qu'elle soit stationnaire. Le modèle ARMA retenu est celui qui minimise le critère AIC. A partir du modèle trouvé, on extrait les paramètres des coefficients.

Dans le code ci-dessous, le modèle SS-ARIMA et le filtre de Kalman sont appliqués à la  variance horaire du Bitcoin.

In [96]:
from utils import optimal_integration_order, find_optimal_arima
observations = df_var_cov['Variance BTC']
d = optimal_integration_order(observations)
arima_model = find_optimal_arima(observations, d)
phi = arima_model['AR coefficients']
theta = arima_model['MA coefficients']

Une fois l'ordre d'intégration optimal trouvé et les coefficients du modèle ARMA estimés on s'en sert pour construire les matrices du modèles espace-état auquel le filtre de Kalman sera appliqué ensuite. Les équations du modèles sont :
$$
\begin{align*}
y_t &= Z \alpha_t + \varepsilon_t \quad \text{(équation d'observation)} \\
\alpha_{t+1} &= T \alpha_t + R \eta_t \quad \text{(équation d'état)}
\end{align*}
$$

Avec 
$$
\varepsilon_t \sim \mathcal{N}(0, H), \quad \eta_t \sim \mathcal{N}(0, Q), \quad \text{and} \quad \alpha_1 \sim \mathcal{N}(a_1, P_1)
$$ 
Les variables sont indépendantes et les matrices $Z, T, R$ ainsi que les matrices de covariance $H$ et $Q$ sont constantes dans le temps.

L'architecture des matrices est la suivante :
$$
Z^T = 
\begin{pmatrix}
1_{d+1} \\
0 \\
\vdots \\
0
\end{pmatrix}, \quad
H = 0, \quad
T =
\begin{pmatrix}
U_d & 1_d^T & 0 & \cdots & 0 \\
0 & \phi_1 & 1 & \cdots & 0 \\
\vdots & \vdots & \ddots & \ddots & \vdots \\
0 & \phi_r & 0 & \cdots & 1 \\
\end{pmatrix}, \quad
R =
\begin{pmatrix}
0_d \\
1 \\
\theta_1 \\
\vdots \\
\theta_{r-1}
\end{pmatrix}, \quad
Q = \sigma^2,
$$

$$
\alpha_t =
\begin{pmatrix}
y_{t-1}^* \\
\vdots \\
\Delta^{d-1} y_{t-1}^* \\
y_t^* \\
\phi_2 y_{t-1}^* + \cdots + \phi_r y_{t-r+1}^* + \theta_1 \eta_t + \cdots + \theta_{r-1} \eta_{t-r+2} \\
\vdots \\
\phi_r y_{t-1}^* + \theta_{r-1} \eta_t
\end{pmatrix},
$$

$$
a_1 =
\begin{pmatrix}
0 \\
\vdots \\
0
\end{pmatrix}, \quad
P_{*,1} =
\begin{pmatrix}
0 & 0 \\
0 & S_r
\end{pmatrix}, \quad
P_{\infty,1} =
\begin{pmatrix}
I_d & 0 \\
0 & 0
\end{pmatrix}, \quad
\eta_t = \xi_{t+1},
$$

Où 
$$
\phi_{p+1} = \cdots = \phi_r = \theta_{q+1} = \cdots = \theta_{r-1} = 0,
$$
$$
1_{d+1} \text{ est un vecteur de 1 de dimension } 1 \times (d+1) \text{, } U_d \text{ est une matrice triangulaire supérieure de dimension} d \times d.
$$

In [97]:
from state_space_models import SSARIMA
ss_model = SSARIMA(d=d, phi=phi, theta=theta) 
ss_model.summary()

State-Space ARIMA Model:
******************************
ARIMA(0,1,4)
AR coefficients (phi): [0. 0. 0. 0. 0.]
MA coefficients (theta): [-0.71627448 -0.18159871  0.23028634 -0.25951237  0.        ]
Variance of noise (sigma^2): 1
******************************
Matrices:
Z: 
[[1. 1. 0. 0. 0. 0.]]

-------------------------
H: 
[[1.e-08]]

-------------------------
T: 
[[1. 1. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0.]
 [0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 0.]]

-------------------------
R: 
[[ 0.        ]
 [ 1.        ]
 [-0.71627448]
 [-0.18159871]
 [ 0.23028634]
 [-0.25951237]]

-------------------------
Q: 
[[1]]

-------------------------
a1: 
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]

-------------------------
P1: 
[[0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0.]
 [0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 1.]]

-------------------------
P1inf: 
[[1. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0.]


Maintenant que le modèle SS-ARIMA est construit, on peut appliquer le filtre de Kalman. Une section dédiée à l'algorithme et à son fonctionnement se trouve en annexe du notebook.

In [98]:
from filters import KalmanFilter
KF = KalmanFilter(ss_model, observations)

Pour mesurer l'efficacité du modèle ainsi que du filtre de Kalman on dispose de plusieurs outils de visualisation.

On peut tout d'abord observer l'évolution de la variance de l'estimation dans le temps.

In [99]:
var = [KF['posteriors'][i].var for i in range(100)]
fig = go.Figure()
fig.add_trace(go.Scatter(y=var, mode='lines', name='Variance'))
fig.update_layout(title='Evolution de la variance de la variance filtrée', xaxis_title='Temps', yaxis_title='Variance')
fig.show()

Celle-ci converge, ce qui montre que la certitude du filtre sur l'état du système grandit au fil des itérations. A partir de seulement une vingtaine d'itérations, le la variance de l'état converge durablement vers 0,54.

Ensuite on peut observer l'évolution dans le temps de la fonction de densité de notre estimation, qui se ressert autour de l'estimation de l'état à mesure que la variance diminue et que la certitude quant au niveau de la variable latente grandit.

In [100]:
from utils import plot_gaussians_plotly

plot_gaussians_plotly(KF['posteriors'][:30])

Enfin on peut comparer graphiquement la volatilité prédite par le modèle SS-ARIMA, la volatilité mesurée et la volatilité filtrée produite par le filtre.

In [101]:
predictions = list()
for prior in KF['priors']:
    predictions.append(float(prior.mean))

volatility_analysis = pd.DataFrame(np.sqrt(predictions),index=df_var_cov.index,columns=['Predicted volatility'])
volatility_analysis['Measured volatility'] = np.sqrt(df_var_cov['Variance BTC'])
volatility_analysis['Filtred volatility'] = np.sqrt(KF['filtered states'])
volatility_analysis['State variance'] = KF['filtered variances']
volatility_analysis.head(5)

Predicted volatility  Measured volatility  \
Timestamp                                                        
2020-02-24 00:00:00              0.000000             0.059683   
2020-02-24 01:00:00              0.042202             0.048310   
2020-02-24 02:00:00              0.042952             0.151693   
2020-02-24 03:00:00              0.110998             0.050296   
2020-02-24 04:00:00              0.079351             0.039369   

                     Filtred volatility  State variance  
Timestamp                                                
2020-02-24 00:00:00            0.024366        0.833333  
2020-02-24 01:00:00            0.044215        1.296988  
2020-02-24 02:00:00            0.076343        1.371571  
2020-02-24 03:00:00            0.104324        1.435249  
2020-02-24 04:00:00            0.070493        1.364218

In [102]:
from utils import filter_plot

plot = filter_plot(title='Analyse de la volatilité filtrée',
                   what='Volatilité',
                   filtred_series=volatility_analysis['Filtred volatility'],
                   prediction_series=volatility_analysis['Predicted volatility'],
                   observation_series=volatility_analysis['Measured volatility'],
                   y_label='Variance')
plot.show()

### III - Application du filtre de Kalman sur un modèle SS-VECH appliqué aux variances et covariances

In [103]:
df_var_cov

Variance BTC  Covariance BTC - ETH  Covariance BTC - LTC  \
Timestamp                                                                       
2020-02-24 00:00:00      0.003562              0.003615              0.003769   
2020-02-24 01:00:00      0.002334              0.002460              0.002598   
2020-02-24 02:00:00      0.023011              0.018212              0.032670   
2020-02-24 03:00:00      0.002530              0.003015              0.003682   
2020-02-24 04:00:00      0.001550              0.001989              0.001750   
...                           ...                   ...                   ...   
2021-04-30 19:00:00      0.002067              0.001359             -0.000330   
2021-04-30 20:00:00      0.006311              0.005542              0.000742   
2021-04-30 21:00:00      0.003593              0.003406              0.000019   
2021-04-30 22:00:00      0.003179              0.001533             -0.000206   
2021-04-30 23:00:00      0.003912              0.002040             -0.000056   

                     Covariance BTC - XRP  Covariance BTC - BCH  Variance ETH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.002974              0.004944      0.006456   
2020-02-24 01:00:00              0.002192              0.003045      0.004312   
2020-02-24 02:00:00              0.030234              0.033199      0.017474   
2020-02-24 03:00:00              0.003008              0.003910      0.004914   
2020-02-24 04:00:00              0.001502              0.002233      0.004236   
...                                   ...                   ...           ...   
2021-04-30 19:00:00             -0.000729              0.002826      0.002067   
2021-04-30 20:00:00              0.001403              0.007724      0.007892   
2021-04-30 21:00:00             -0.000799              0.004410      0.005096   
2021-04-30 22:00:00              0.000205              0.002362      0.002911   
2021-04-30 23:00:00              0.000195              0.003833      0.001896   

                     Covariance ETH - LTC  Covariance ETH - XRP  \
Timestamp                                                         
2020-02-24 00:00:00              0.005494              0.004639   
2020-02-24 01:00:00              0.003471              0.002857   
2020-02-24 02:00:00              0.028066              0.025975   
2020-02-24 03:00:00              0.005075              0.004252   
2020-02-24 04:00:00              0.002850              0.002298   
...                                   ...                   ...   
2021-04-30 19:00:00             -0.000155             -0.001634   
2021-04-30 20:00:00              0.000175              0.000646   
2021-04-30 21:00:00             -0.000290             -0.000466   
2021-04-30 22:00:00             -0.000432              0.000546   
2021-04-30 23:00:00              0.000380             -0.000136   

                     Covariance ETH - BCH  Variance LTC  Covariance LTC - XRP  \
Timestamp                                                                       
2020-02-24 00:00:00              0.006757      0.007723              0.004649   
2020-02-24 01:00:00              0.004696      0.007448              0.003595   
2020-02-24 02:00:00              0.029274      0.057310              0.050088   
2020-02-24 03:00:00              0.005020      0.012367              0.006036   
2020-02-24 04:00:00              0.004074      0.004465              0.001664   
...                                   ...           ...                   ...   
2021-04-30 19:00:00              0.002303      0.002584              0.002218   
2021-04-30 20:00:00              0.007030      0.009715              0.011768   
2021-04-30 21:00:00              0.005644      0.004015              0.005075   
2021-04-30 22:00:00              0.002475      0.006612              0.003225   
2021-04-30 23:00:00              0.002039      0.011335              

Dans cette partie nous proposons d'utiliser un modèle espace-état VECH pour modéliser à la fois les variances des actifs mais également leurs covariances en appliquant un Unscented Kalman Filter sur ce dernier. Nous avons retenu l'Unscented Kalman Filter plutôt que l'Extented Kalman Filter car ce premier filtre est moins complexe numériquement que le second mais aussi en surtout en raison du fait qu'il est moins gourmand en ressources informatiques et donc en temps de calcul, ce qui constitue un point non négligeable lorsque l'on possède 15 séries de 15,349 données chacune. L'UKF fournit de surcroît des performances souvent équivalentes à celle de l'EKF, ce qui justifie d'autant plus son utilisation dans ce contexte.

Le modèle Vech(p,q) peut être résumé par l'équation matricielle suivante :

$$
\text{Vech}(H_t) =
\begin{pmatrix}
\sigma^2_{1t} \\
\sigma_{12t} \\
\sigma^2_{2t}
\end{pmatrix}
= \gamma + \sum_{j=1}^q A_j \, \text{Vech}(U_{t-j} U_{t-j}^\prime) + \sum_{j=1}^p B_j \, \text{Vech}(H_{t-j}),
$$

où la fonction $\text{Vech}(X)$ transforme une matrice symétrique $X$ en un vecteur contenant ses éléments uniques empilés ligne après ligne.

Pour construire un modèle espace-état adapté au modèle VECH et ensuite appliquer un Unscented Kalman Filter sur ce dernier, il faut d'abord estimer le modèle VECH optimal à partir des données. Une fois ce dernier estimé, il suffit d'en extraire les matrices $\{A_i\}_{i=1}^q$ et $\{B_i\}_{i=1}^p$ ainsi que le vecteur de constantes $\gamma$.

In [104]:
from utils import VECHModel

variances = df_var_cov[[col for col in df_var_cov.columns if 'Variance' in col]].values
covariances = df_var_cov[[col for col in df_var_cov.columns if 'Covariance' in col]].values

vech_model = VECHModel(max_p=1,max_q=1)
vech_model.fit(variances,covariances)

Le modèle SS-VECH se présente de la manière suivante :
$$
\begin{align*}
y_t &= Z \alpha_t + \varepsilon_t \quad \text{(équation d'observation)} \\
\alpha_{t+1} &= T \alpha_t + R f(\eta_t) \quad \text{(équation d'état)}
\end{align*}
$$
Avec
$$f(X) = \text{Vech}(X X^T)$$
Et
$$
\varepsilon_t \in \mathbb{R}^{\frac{n(n+1)}{2}} \sim \mathcal{N}(0, H), \quad \eta_t \in \mathbb{R}^{\frac{n(n+1)}{2} + \frac{n(n+1)}{2}(q+p)} \sim \mathcal{N}(0, Q), \quad \text{and} \quad \alpha_1 \sim \mathcal{N}(a_1, P_1)
$$
Les variables sont indépendantes et les matrices $Z, T, R$ ainsi que les matrices de covariance $H$ et $Q$ sont constantes dans le temps.


L'architecture des matrices est la suivante :
$$
\alpha_t =
\begin{pmatrix}
1 \\
\text{Vech}(H_t) \\
\text{Vech}(H_{t-1}) \\
\text{Vech}(H_{t-p+1}) \\
f(\eta_t) \\
f(\eta_{t-1}) \\
f(\eta_{t-p+1})
\end{pmatrix}
$$

$$
\forall t \quad \alpha_t \in \mathbb{R}^{\frac{n(n+1)}{2}(q+p)}
$$

$$
Z =
\begin{bmatrix}
0 & I_{\frac{n(n+1)}{2}} & 0 & \cdots & 0
\end{bmatrix}
$$

$$
Z \in \mathbb{R}^{\frac{n(n+1)}{2} \times \frac{n(n+1)}{2}(q+p)}
$$

$$
T =
\begin{pmatrix}
1 & 0 & 0 & \cdots & 0 & 0 & 0 & 0 & 0 & 0 & 0 \\
\gamma & B_1 & B_2 & \cdots & B_{p-1} & B_p & A_1 & A_2 & \cdots & A_{q-1} & A_q \\
0 & I_{\frac{n(n+1)}{2}} & 0 & 0 & \cdots & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & I_{\frac{n(n+1)}{2}} & 0 & \cdots & 0 & 0 & 0 & 0 & 0 & 0 \\
\vdots & \vdots & \vdots & \ddots & \cdots & \vdots & \vdots & \vdots & \vdots & \vdots & \vdots \\
0 & 0 & 0 & 0 & I_{\frac{n(n+1)}{2}} & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & I_{\frac{n(n+1)}{2}} & 0 & 0 & 0 & 0 \\
\vdots & \vdots & \vdots & \vdots & \vdots & \vdots & \vdots & \ddots & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 & I_{\frac{n(n+1)}{2}} & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 & 0 & I_{\frac{n(n+1)}{2}} & 0
\end{pmatrix}
$$

$$
T \in \mathbb{R}^{\frac{n(n+1)}{2}(q+p) \times \frac{n(n+1)}{2}(q+p)}
$$

$$
R =
\begin{pmatrix}
0 & \cdots & 0 & \cdots & 0 & \cdots & 0\\
\vdots & \ddots & \vdots & \ddots & \vdots & \ddots & \vdots \\
0 & \cdots & I_{\frac{n(n+1)}{2}} & \cdots & 0 & \cdots & 0\\
\vdots & \ddots & \vdots & \ddots & \vdots & \ddots & \vdots\\
0 & \cdots & \cdots & \cdots & 0 & \cdots & 0
\end{pmatrix}
$$

$$
R \in \mathbb{R}^{\frac{n(n+1)}{2}(q+p) \times \left[\frac{n(n+1)}{2} + \frac{n(n+1)}{2}(q+p)\right]}
$$

Dans la matrice $R$, la sous-matrice identité $I_{\frac{n(n+1)}{2}}$ se trouve à la $2 + p\frac{n(n+1)}{2}$ème ligne et à la $2+(p+q)\frac{n(n+1)}{2}$ème colonne.

A partir de la classe SSVECH on peut construire le modèle espace-état adapté au modèle VECH estimé précédemment en indiquant en entrées le nombre d'actifs, les matrices $\{A_i\}_{i=1}^q$ et $\{B_i\}_{i=1}^p$ ainsi que le vecteur de constantes $\gamma$.

In [105]:
from state_space_models import SSVECH 
ssvech = SSVECH(n=len(cryptos),A=vech_model.A_matrices,B=vech_model.B_matrices,gamma=vech_model.gamma,observation_noise=2e-1)
ssvech.summary()

State-Space VECH Model:
******************************
AR matrices (B):
B_0:
[[0.08407082 0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.        ]
 [0.         0.07427246 0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.        ]
 [0.         0.         0.14484825 0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.        ]
 [0.         0.         0.         0.02217791 0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.        ]
 [0.         0.         0.         0.         0.00640969 0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.        ]
 [0.         0.         0.         0.         0.         0.04581689
  0.         0.         0.         0.         0.         0.
  0.         0.

Maintenant que le modèle SS-VECH est généré on peut appliquer l'Unscented Kalman Filter au modèle. Plus de détails sur l'algorithme et son fonctionnement se trouvent en annexe dans une section dédiée.

In [106]:
from filters import UnscentedKalmanFilter
UKF = UnscentedKalmanFilter(ssvech,df_var_cov.values)

In [107]:
filtered_states_df = pd.DataFrame(UKF['filtered states'], index=df_var_cov.index,columns=df_var_cov.columns)
filtered_states_df.head(5)

Variance BTC  Covariance BTC - ETH  Covariance BTC - LTC  \
Timestamp                                                                       
2020-02-24 00:00:00      0.002224              0.000625              0.004305   
2020-02-24 01:00:00      0.130617             -0.002539             -0.024123   
2020-02-24 02:00:00      0.152168             -0.000317             -0.004633   
2020-02-24 03:00:00      0.137888             -0.002732             -0.026297   
2020-02-24 04:00:00      0.135802             -0.003275             -0.032854   

                     Covariance BTC - XRP  Covariance BTC - BCH  Variance ETH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.001950              0.003919      0.001417   
2020-02-24 01:00:00             -0.010435             -0.021171     -0.000992   
2020-02-24 02:00:00             -0.000751             -0.001188     -0.000097   
2020-02-24 03:00:00             -0.011051             -0.022361     -0.001114   
2020-02-24 04:00:00             -0.012755             -0.025485     -0.001309   

                     Covariance ETH - LTC  Covariance ETH - XRP  \
Timestamp                                                         
2020-02-24 00:00:00              0.000186              0.000211   
2020-02-24 01:00:00              0.002101              0.001221   
2020-02-24 02:00:00              0.000280              0.000205   
2020-02-24 03:00:00              0.002199              0.001265   
2020-02-24 04:00:00              0.002654              0.001559   

                     Covariance ETH - BCH  Variance LTC  Covariance LTC - XRP  \
Timestamp                                                                       
2020-02-24 00:00:00              0.001372      0.000830              0.000581   
2020-02-24 01:00:00              0.001593      0.000448             -0.001984   
2020-02-24 02:00:00              0.000444      0.000058             -0.000292   
2020-02-24 03:00:00              0.001353      0.000389             -0.002164   
2020-02-24 04:00:00              0.001733      0.000470             -0.002631   

                     Covariance LTC - BCH  Variance XRP  Covariance XRP - BCH  \
Timestamp                                                                       
2020-02-24 00:00:00              0.000980      0.000692             -0.000154   
2020-02-24 01:00:00              0.001249      0.000560              0.002527   
2020-02-24 02:00:00              0.000254      0.000077              0.000390   
2020-02-24 03:00:00              0.001148      0.000518              0.002696   
2020-02-24 04:00:00              0.001438      0.000628              0.003294   

                     Variance BCH  
Timestamp                          
2020-02-24 00:00:00      0.000763  
2020-02-24 01:00:00      0.000250  
2020-02-24 02:00:00      0.000029  
2020-02-24 03:00:00      0.000198  
2020-02-24 04:00:00      0.000237

In [108]:
predictions = list()
for prior in UKF['priors']:
    predictions.append(prior.mean)

predicted_var_cov = pd.DataFrame(predictions,index=filtered_states_df.index,columns=df_var_cov.columns)
predicted_var_cov.head(5)

Variance BTC  Covariance BTC - ETH  Covariance BTC - LTC  \
Timestamp                                                                       
2020-02-24 00:00:00  3.597909e-17         -9.288185e-18          1.830862e-17   
2020-02-24 01:00:00  2.227622e-01          5.130119e-04          5.035926e-03   
2020-02-24 02:00:00  2.194255e-01         -2.755850e-03         -2.777020e-02   
2020-02-24 03:00:00  2.326005e-01         -1.511040e-04         -1.877529e-03   
2020-02-24 04:00:00  2.193750e-01         -2.912354e-03         -2.942891e-02   

                     Covariance BTC - XRP  Covariance BTC - BCH  Variance ETH  \
Timestamp                                                                       
2020-02-24 00:00:00          7.419248e-19         -1.477175e-17  2.289842e-18   
2020-02-24 01:00:00          1.943656e-03          3.874941e-03  2.559851e-04   
2020-02-24 02:00:00         -1.068721e-02         -2.131675e-02 -1.096634e-03   
2020-02-24 03:00:00         -5.362649e-04         -1.060239e-03 -5.669834e-05   
2020-02-24 04:00:00         -1.127964e-02         -2.249682e-02 -1.160394e-03   

                     Covariance ETH - LTC  Covariance ETH - XRP  \
Timestamp                                                         
2020-02-24 00:00:00         -8.595611e-19          4.460104e-18   
2020-02-24 01:00:00         -3.587337e-04         -1.880072e-04   
2020-02-24 02:00:00          2.240399e-03          1.322929e-03   
2020-02-24 03:00:00          1.263619e-04          8.321472e-05   
2020-02-24 04:00:00          2.362849e-03          1.393317e-03   

                     Covariance ETH - BCH  Variance LTC  Covariance LTC - XRP  \
Timestamp                                                                       
2020-02-24 00:00:00         -2.895061e-18  8.950228e-18         -2.452491e-18   
2020-02-24 01:00:00          1.102105e-04  7.119600e-06          4.242283e-04   
2020-02-24 02:00:00          1.557604e-03  4.034225e-04         -2.216148e-03   
2020-02-24 03:00:00          1.637470e-04  2.317327e-05         -1.289242e-04   
2020-02-24 04:00:00          1.566090e-03  4.183716e-04         -2.345641e-03   

                     Covariance LTC - BCH  Variance XRP  Covariance XRP - BCH  \
Timestamp                                                                       
2020-02-24 00:00:00          3.489162e-18  1.415366e-17         -1.234194e-18   
2020-02-24 01:00:00         -3.371949e-05 -2.247799e-05         -4.733984e-04   
2020-02-24 02:00:00          1.248462e-03  5.370248e-04          2.782175e-03   
2020-02-24 03:00:00          9.268776e-05  3.134289e-05          1.662126e-04   
2020-02-24 04:00:00          1.290214e-03  5.598529e-04          2.939220e-03   

                     Variance BCH  
Timestamp                          
2020-02-24 00:00:00  2.890829e-18  
2020-02-24 01:00:00  2.507877e-05  
2020-02-24 02:00:00  2.047391e-04  
2020-02-24 03:00:00  1.141360e-05  
2020-02-24 04:00:00  2.109891e-04

In [109]:
plot = filter_plot(title='Analyse de la variance filtrée du Bitcoin',
                   what='Variance',
                   filtred_series=filtered_states_df['Variance BTC'],
                   prediction_series=predicted_var_cov['Variance BTC'],
                   observation_series=df_var_cov['Variance BTC'],
                   y_label='Variance')
plot.show()

In [110]:
plot = filter_plot(title='Analyse de la covariance filtrée entre Bitcoin et Ethereum',
                   what='Covariance',
                   filtred_series=filtered_states_df['Covariance BTC - ETH'],
                   prediction_series=predicted_var_cov['Covariance BTC - ETH'],
                   observation_series=df_var_cov['Covariance BTC - ETH'],
                   y_label='Covariance')
plot.show()

In [114]:
from utils import plot_gaussians_3d_plotly
gaussians = []
for i in range(10000,df_var_cov.shape[0]):
    mean = UKF['state estimates'][i].mean[:2]
    cov = UKF['state estimates'][i].var[:2,:2]
    gaussians.append(gaussian(mean,cov))

fig = plot_gaussians_3d_plotly(gaussians)
fig.show()

ImportError: cannot import name 'plot_gaussians_3d_plotly' from 'utils' (c:\Users\rabhi\Documents\Master 272 IEF - Dauphine\M2\S1\Gestion quantitative\Soutenance\repo\Projet-Gestion-Quant\Code\utils.py)

### Annexe

#### Kalman Filter

**1 - <u>Initialisation**</u>  
**a. Initialisation de l'état du système**

$$a_1 =
\begin{pmatrix}
0 \\
\vdots \\
0
\end{pmatrix}$$

**b. Initialisation de la croyance en l'état du système**
$$P_1 =
\begin{pmatrix}
0 & 0 \\
0 & S_r
\end{pmatrix}$$


**2 - <u>Prédiction**</u>   
**a. Prédiction de l'état latent $\bar{\alpha}_t$**  
On se sert du process model donné par l'équation d'état pour calculer la prédiction de l'état du système $\bar{\alpha}_t$ à partir de l'état filtré de la période précédente $\alpha_{t-1}$ :
$$\bar{\alpha}_t = T \alpha_{t-1} + R \eta_{t}$$
**b. Prédiction de la covariance de l'état latent $\bar{P}_t$**  
On calcule également la covariance de la prédiction de l'état du système $\bar{P}_t$ à partir de la covariance de l'état filtré de la période précédente $P_{t-1}$ : 
$$\bar{P}_t = TP_{t-1}T^T+RQR^T$$  

Cela revient en fait à calculer le prior du modèle en faisant la somme de deux variables aléatoires gaussiennes ($\alpha_{t-1} \sim \mathcal{N}(a_{t-1},P_{t-1})$ et $\eta_t \sim \mathcal{N}(0,Q)$), somme qui donne une nouvelle variable gaussienne :
$$\bar{\alpha}_t \sim \mathcal{N}(\underbrace{Ta_{t-1}+R\cdot 0}_{\text{somme des moyennes des gaussiennes}},\underbrace{TP_{t-1}T^T+RQR^T}_{\text{somme des variances des gaussiennes}})$$

**3 - <u>Mise à jour**</u>  
**a. Calcul de l'innovation**  
$$v_t = y_t - Z^T \bar{\alpha}_t$$
**b. Calcul de la variance de l'innovation**  
$$F_t = Z^T \bar{P}_t Z + H$$
**c. Calcul du gain de Kalman $K_t$**  
$$K_t = \bar{P}_t Z F_t^{-1}$$
**d. Mise à jour de la moyenne de l'état latent $\alpha_t$**  
$$a_t = \bar{a_t} + K_t v_t$$
**e. Mise à jour de la covariance $P_t$**  
$$P_t=(I-K_tZ^T)\bar{P}_t$$  

Encore une fois cette étape revient à calculer le posterior en effectuant le produit de deux gaussiennes ($\bar{\alpha}_t \sim \mathcal{N}(T\bar{a}_{t}+R\cdot 0,TP_{t-1}T^T+RQR^T)$ et $y_t \sim \mathcal{N}(y_t,H)$), produit qui donne une gaussienne :
$$\alpha_t \sim \mathcal{N}(P_t \cdot (\bar{P}_t^{-1} \bar{a}_t + Z F^{-1} y_t),(\bar{P}_t^{-1} + Z F^{-1} Z^T)^{-1}) $$

#### Unscented Kalman Filter

L'application de l'algorithme de l'UKF permet d'étendre l'utilisation du filtre de Kalman à des systèmes non linéaires. Lorsque l'on applique un filtre de Kalman, $T$ et $Z$ sont représentées par des matrices, toutefois elles peuvent également prendre la forme de fonctions non-linéaires pour lesquelles ce filtre de Kalman diverge. En effet, si l'on applique une fonction non-linéaire à des observations issues d'une distribution gaussienne, la distribution de sortie n'est plus gaussienne et l'hypothèse de "gaussienneté" des innovations du modèle n'est plus respectée.

**1 - <u>Sigma points**</u> 

L'idée derrière l'UKF est de sélectionner des points représentatifs de la distribution gaussienne appelés *sigma points* $\boldsymbol\chi_{i=1}^{2n+1}$ et d'appliquer la fonction non-linéaire sur ces derniers. Les sigmas points transformés $\mathcal{Y}_{i=1}^{2n+1}$ obtenus en sortie sont ensuite pondérés par des poids puis utilisées pour calculer la moyenne et la covariance. Pour sélectionner les points on applique l'algorithme de Rudolph Van der Merwe qui permet d'obtenir un bon arbitrage entre performance et précision. En suivant ce dernier, les sigmas points retenus sont les suivants :
$$
\begin{cases}
\mathcal{X}_0 = \mu \\
\mathcal{X}_i = \mu +  \left[\sqrt{(n+\lambda)\Sigma} \right]_i, \text{for} & i=1..n \\
\mathcal{X}_i = \mu - \left[\sqrt{(n+\lambda)\Sigma}\right]_{i-n}, \text{for} & i=(n+1)..2n
\end{cases}
$$
L'indice $i$ dans $[\sqrt{(n+\lambda)\Sigma}]_i$ indique que l'on choisit le i-ème vecteur colonne de la matrice.  

Pour ce qui est des poids appliqués aux sigmas points transformés, ils sont obtenus de la manière suivante après avoir fixé trois paramètres, $\alpha$, $\beta$ et $\kappa$ :
$$
\begin{aligned}
\lambda&=\alpha^2(n+\kappa)-n \\ 
W^m_0 &= \frac{\lambda}{n+\lambda} \\
W^c_0 &= \frac{\lambda}{n+\lambda} + 1 -\alpha^2 + \beta \\
W^m_i = W^c_i &= \frac{1}{2(n+\lambda)}\;\;\;i=1..2n
\end{aligned}
$$


**2 - <u>Prédiction**</u>  

Pour rappel, le modèle SS-VECH est synthétisé par le système d'équations suivantes :
$$
\begin{align*}
y_t &= Z \alpha_t + \varepsilon_t \quad \text{(équation d'observation)} \\
\alpha_{t+1} &= T \alpha_t + R f(\eta_t) \quad \text{(équation d'état)}
\end{align*}
$$

Dans le cadre de ce modèle, c'est la fonction $f$ qui implique une transformation non-linéaire des résidus du modèle. Pour l'étape de prédiction, on sélectionne donc les sigmas points $\boldsymbol\chi_{i=1}^{2n+1}$ issus de la distribution gaussienne suivie par les résidus et on applique la fonction $f$ sur chacun d'eux. Une fois que l'on a les sigmas points transformés $\mathcal{Y}_{i=1}^{2n+1}=f(\boldsymbol\chi_{i=1}^{2n+1})$, on applique l'unscented transform en calculant la moyenne et la covariance de la distribution de sortie en utilisant les poids calculés par l'algorithme de Van der Merwe :
$$\begin{aligned}
\mu &= \sum_i w^m_if(\mathcal{X}_i) \\
\Sigma &= \sum_i w_i^c{(f(\mathcal{X}_i)-\mu)(f(\mathcal{X}_i)-\mu)^\mathsf{T}}
\end{aligned}
$$

A partir de ces éléments on peut réappliquer le filtre de Kalman linéaire en effectuant une somme de gaussiennes pour déterminer la prédiction de l'état du système :
$$
T\alpha_{t-1} + Rf(\eta_t) = \bar{\alpha}_t \sim \mathcal{N}(\underbrace{Ta_{t-1}+\mu}_{\text{somme des moyennes des gaussiennes}},\underbrace{TP_{t-1}T^T+R \Sigma}_{\text{somme des variances des gaussiennes}})
$$

**3 - <u>Mise à jour**</u>  

Pour l'étape de mise à jour, le modèle SS-VECH n'implique pas de fonction non-linéaire car $Z$ est une matrice donc le filtre de Kalman classique peut-être appliqué comme pour le SS-ARIMA. Toutefois pour garder une fonction UKF générale l'algorithme suivant s'applique à l'étape de mise à jour :

**a. Unscented transform**

Le filtre de Kalman effectue la mise à jour dans l'espace de mesure donc on convertit les sigmas points transformés du prior en mesure en utilisant la fonction de mesure $Z$ (qui dans notre cas est une simple multiplication matricielle) :
$$\boldsymbol{\mathcal{Z}} = Z(\boldsymbol{\mathcal{Y}})$$

On obtient alors de nouveaux sigmas points transformés pour lesquels on va appliquer l'unscented transform :

$$\begin{aligned}
\boldsymbol\mu_z &= \sum_{i=0}^{2n} w^m_i\boldsymbol{\mathcal Z}_i \\
\mathbf P_z &= \sum_{i=0}^{2n} w^c_i{(\boldsymbol{\mathcal Z}_i-\boldsymbol{\mu}_z)(\boldsymbol{\mathcal Z}_i-\boldsymbol{\mu}_z)^\mathsf T} + H
\end{aligned}
$$

**b. Calcul de l'innovation**

On peut ensuite calculer les innovations comme pour un filtre de Kalman linéaire :
$$v_t = y_t - \boldsymbol\mu_z$$

**c. Calcul du gain de Kalman $K_t$** 

Afin d'obtenir le gain de Kalman on calcule d'abord la variance croisée de l'état et des observations définie par :
$$\mathbf P_{xz} =\sum_{i=0}^{2n} w^c_i(\boldsymbol{\mathcal Y}_i-\bar a_t)(\boldsymbol{\mathcal Z}_i-\boldsymbol\mu_z)^\mathsf T$$

Le gain de Kalman est alors donné par :
$$K = \mathbf P_{xz} \mathbf P_z^{-1}$$

**d. Mise à jour de la moyenne de l'état latent $\alpha_t$**  
$$a_t = \bar{a_t} + K_t v_t$$

**e. Mise à jour de la covariance $P_t$**  
$$P_t=(I-K_tZ^T)\bar{P}_t$$ 
